# LangChain全面剖析之Retrieval

## 1. Retrieval模块的设计意义

### 1.1 LangChain版本升级

LangChain 5月12日预发布了2.0版本，该版本对于我们用户来说API几乎没变化，我们使用时直接升级即可

1. 自己整理了底层的API，让整个框架更稳定，更安全
2. 加强了LangGraph的功能
3. Doc发生了变化，把langchain-core和langchain-community梳理的更清晰

文档链接：[https://python.langchain.com/v0.2/docs/](https://python.langchain.com/v0.2/docs/)

In [ ]:
# ! pip install --upgrade langchain
# ! pip install --upgrade openai
! pip install langchain==0.2.0
! pip install openai==1.30.1

In [1]:
import langchain

print(langchain.__version__)

0.2.0


In [2]:
import openai

print(openai.__version__)

1.30.1


### 1.2 RAG架构

#### (1) 介绍

&emsp;&emsp;目前，已经出现了非常多的产品是几乎完全建立在 RAG 之上，包括客服系统、基于大模型的数据分析，以及成千上万的数据驱动聊天应用，应用场景五花八门，但其需要解决的核心问题都是一个：如何与私域数据交互。而私域数据主要的问题是：需要有效地将企业数据整合进大语言模型中，但由于大模型的上下文处理能力有限，必须精准的选择出哪些数据在当前对话上下文中是有效的。

&emsp;&emsp;一个系统是否能成功地商业化落地，在很大程度上取决于复杂的市场环境，大模型的核心优势在于其内容生成的多样性和创新性，但这同样也是其最大的问题，因为大模型生成的内容是不可控的，尤其是在金融和医疗领域等领域，一次金额评估的错误，一次医疗诊断的失误，哪怕只出现一次都是致命的。此外，大模型有时也会输出看似合理但实则错误的信息，这对于非专业人士来说可能难以辨识，但从专业角度来看却存在着不小的问题。这些都是大模型当前面临的挑战，而且目前还没有能够百分之百解决这种情况的方案。

&emsp;&emsp;通过人们不断地对大模型领域的探索，非常多的实验能够证明，当为大模型提供一定的上下文信息后，其输出会变得更稳定。那么，将知识库中的信息或掌握的信息先输送给大模型，再由大模型服务用户，就是大家普遍达成共识的一个结论和方法。传统的对话系统、搜索引擎等核心依赖于检索技术，如果将这一检索过程融入大模型应用的构建中，既可以充分利用大模型在内容生成上的能力，也能通过引入的上下文信息显著约束大模型的输出范围和结果，同时还实现了将私有数据融入大模型中的目的，达到了双赢的效果。所以我们才看到RAG的实现是包括两个阶段的：检索阶段和生成阶段。在检索阶段，从知识库中找出与问题最相关的知识，为后续的答案生成提供素材。在生成阶段，RAG会将检索到的知识内容作为输入，与问题一起输入到语言模型中进行生成。这样，生成的答案不仅考虑了问题的语义信息，还考虑了相关私有数据的内容。

&emsp;&emsp;综合上述分析，当应用需求集中在利用大模型去回答特定私有领域的知识，且知识库足够大，那么除了微调大模型外，RAG就是非常有效的一种解决方案。LangChain对这一流程提供了解决方案。

#### (2) 模块及文档

为了方便阅读，先跳到老版API文档

* Introduction: [https://python.langchain.com/v0.1/docs/modules/data_connection/](https://python.langchain.com/v0.1/docs/modules/data_connection/)
* Document Loader（Langchain提供的加载工具）：[https://python.langchain.com/v0.1/docs/modules/data_connection/document_loaders/](https://python.langchain.com/v0.1/docs/modules/data_connection/document_loaders/)
* Document Transformer（Langchain提供的不同文本的切割工具）：[https://python.langchain.com/v0.1/docs/modules/data_connection/document_transformers/](https://python.langchain.com/v0.1/docs/modules/data_connection/document_transformers/)
* Embedding（支持的Embedding模型）：[https://python.langchain.com/v0.1/docs/modules/data_connection/text_embedding/](https://python.langchain.com/v0.1/docs/modules/data_connection/text_embedding/)
* Vector Store（支持的向量数据库）：[https://python.langchain.com/v0.1/docs/modules/data_connection/vectorstores/](https://python.langchain.com/v0.1/docs/modules/data_connection/vectorstores/)
* Retrieve（支持的检索策略）：[https://python.langchain.com/v0.1/docs/modules/data_connection/retrievers/](https://python.langchain.com/v0.1/docs/modules/data_connection/retrievers/)


## 3 Source 与 Document Loaders

#### 3.1 介绍

`Source`概念指的是RAG架构中所外挂的知识库。

正如我们之前所讨论的，因为大模型的原生能力很强，所以它可以识别多种不同的类型的原始数据而不用做额外的处理，而且在实际场景中，私有数据通常也并不是单一的，可以来自多种不同的形式，可以是上百个.csv文件，可以是上千个.json文件，也可以是上万个.pdf文件，同时如果对接到具体的业务，可以是某一个业务流程外放的API，可以是某个网站的实时数据等多种情况。

`Document Loaders`是文档加载器

LangChain将常见的数据格式和数据来源使用LangChain的规范，抽象出一个一个的单独的集成模块，称为文档加载器（Document loaders），用于快速加载某种形式下的文本数据。

Langchain封装好的loader地址：
[https://python.langchain.com/v0.1/docs/integrations/document_loaders/](https://python.langchain.com/v0.1/docs/integrations/document_loaders/) 

下面是各种文档加载器的介绍

### 3.2 加载txt文档

#### (1) 数据及科学上网设置

文档见附带的zip文件，解压后放到data目录下

In [5]:
## 设置科学上网
import subprocess
import os

result = subprocess.run('bash -c "source /etc/network_turbo && env | grep proxy"', shell=True, capture_output=True, text=True)
output = result.stdout
for line in output.splitlines():
    if '=' in line:
        var, value = line.split('=', 1)
        os.environ[var] = value

#### (2) 加载文件

In [9]:
from langchain.document_loaders import TextLoader

docs = TextLoader('./data/langchain.txt', encoding="utf-8").load()

#### (3) 查看加载后得到的对象

In [10]:
docs

[Document(page_content='LangChain 是一个用于开发由大型语言模型 (LLMs) 驱动的应用程序的框架。LangChain简化了LLM应用程序生命周期的每个阶段。\nLangChain 已经成为了我们每一个大模型开发工程师的标配。', metadata={'source': './data/langchain.txt'})]

#### (4) 查看对象类型

In [11]:
type(docs[0])

langchain_core.documents.base.Document

#### (5) 查看对象内加载的数据

In [12]:
docs[0].page_content

'LangChain 是一个用于开发由大型语言模型 (LLMs) 驱动的应用程序的框架。LangChain简化了LLM应用程序生命周期的每个阶段。\nLangChain 已经成为了我们每一个大模型开发工程师的标配。'

In [13]:
docs[0].page_content[:30]

'LangChain 是一个用于开发由大型语言模型 (LLMs'

#### (6) 查看元数据

In [14]:
docs[0].metadata

{'source': './data/langchain.txt'}

### 3.3 加载pdf

#### (1) 安装依赖

In [15]:
! pip install pypdf

Looking in indexes: http://mirrors.aliyun.com/pypi/simple
     |████████████████████████████████| 290 kB 109.7 MB/s eta 0:00:01


#### (2) 加载文件

In [16]:
from langchain_community.document_loaders import PyPDFLoader

loader = PyPDFLoader("./data/本地知识库.pdf")
pages = loader.load_and_split()

#### (3) 加载后得到的对象

In [17]:
pages

[Document(page_content='1.WhatisLangChain?\nLangChainisaframeworkfordevelopingapplicationspoweredbylanguagemodels.Itenables\napplicationsthat:\n\uf0b7Arecontext-aware:connectalanguagemodeltosourcesofcontext(promptinstructions,\nfewshotexamples,contenttogrounditsresponsein,etc.)\n\uf0b7Reason:relyonalanguagemodeltoreason(abouthowtoanswerbasedonprovided\ncontext,whatactionstotake,etc.)\nThisframeworkconsistsofseveralparts.\n\uf0b7LangChainLibraries:ThePythonandJavaScriptlibraries.Containsinterfacesand\nintegrationsforamyriadofcomponents,abasicruntimeforcombiningthesecomponents\nintochainsandagents,andoff-the-shelfimplementationsofchainsandagents.\n\uf0b7LangChainTemplates:Acollectionofeasilydeployablereferencearchitecturesforawide\nvarietyoftasks.\n\uf0b7LangServe:AlibraryfordeployingLangChainchainsasaRESTAPI.\n\uf0b7LangSmith:Adeveloperplatformthatletsyoudebug,test,evaluate,andmonitorchains\nbuiltonanyLLMframeworkandseamlesslyintegrateswithLangChain.\n2.WhatisLECL?\nLangChainExpressionL

#### (4) 查案对象类型

In [21]:
type(pages[0])

langchain_core.documents.base.Document

#### (5) 查看加载的文档数据

In [22]:
pages[0].page_content

'1.WhatisLangChain?\nLangChainisaframeworkfordevelopingapplicationspoweredbylanguagemodels.Itenables\napplicationsthat:\n\uf0b7Arecontext-aware:connectalanguagemodeltosourcesofcontext(promptinstructions,\nfewshotexamples,contenttogrounditsresponsein,etc.)\n\uf0b7Reason:relyonalanguagemodeltoreason(abouthowtoanswerbasedonprovided\ncontext,whatactionstotake,etc.)\nThisframeworkconsistsofseveralparts.\n\uf0b7LangChainLibraries:ThePythonandJavaScriptlibraries.Containsinterfacesand\nintegrationsforamyriadofcomponents,abasicruntimeforcombiningthesecomponents\nintochainsandagents,andoff-the-shelfimplementationsofchainsandagents.\n\uf0b7LangChainTemplates:Acollectionofeasilydeployablereferencearchitecturesforawide\nvarietyoftasks.\n\uf0b7LangServe:AlibraryfordeployingLangChainchainsasaRESTAPI.\n\uf0b7LangSmith:Adeveloperplatformthatletsyoudebug,test,evaluate,andmonitorchains\nbuiltonanyLLMframeworkandseamlesslyintegrateswithLangChain.\n2.WhatisLECL?\nLangChainExpressionLanguage,orLCEL,isadecla

In [23]:
pages[0].page_content[:30]

'1.WhatisLangChain?\nLangChainis'

#### (6) 查看元数据

In [25]:
pages[0].metadata

{'source': './data/本地知识库.pdf', 'page': 0}

### 3.4 API总结

#### (1) 相同的使用方式

同样，对于`TextLoader`，依然是使用`.page_content`和`.metadata`去访问数据，也就是说，每一个文档加载器虽然代码逻辑不同，应用需求不同，但**使用方式是相同的**。

这就需要我们去理解为什么要这样做。这其实很容易想到，对于**Sourch**中多种不同的数据源，要想能在接下来的流程中可以用一种统一的形式检索、调用，至少要保证的是：把它们以一种**相对统一的方式**读取出来。

所以LangChain的设计就是对于每一个在LangChain中集成的文档加载器，都要继承自**BaseLoader** and **Document Class**基类，当不同来源的数据通过`load`方法加载进来后，全部转化成**Documents**对象。

实现逻辑如下所示：

#### (2) BaseLoader基类

`BaseLoader` 类定义了如何从不同的数据源加载文档，每个基于不同数据源实现的`loader`，都需要集成`BaseLoader`。Baseloader要求不对，对于任何具体实现的loader，最少都要实现 load方法。
```python
class BaseLoader(ABC):
    """文档加载器接口。

    实现应当使用生成器实现延迟加载方法，以避免一次性将所有文档加载进内存。

    `load` 方法仅供用户方便使用，不应被重写。
    """

    # 子类不应直接实现此方法。而应实现延迟加载方法。
    def load(self) -> List[Document]:
        """将数据加载为 Document 对象。"""
        return list(self.lazy_load())

    def load_and_split(
        self, text_splitter: Optional[TextSplitter] = None
    ) -> List[Document]:
        """加载文档并将其分割成块。块以 Document 形式返回。

        不要重写此方法。它应被视为已弃用！

        参数:
            text_splitter: 用于分割文档的 TextSplitter 实例。默认为 RecursiveCharacterTextSplitter。

        返回:
            文档列表。
        """
                .....
                .....
            _text_splitter: TextSplitter = RecursiveCharacterTextSplitter()
        else:
            _text_splitter = text_splitter
        docs = self.load()
        return _text_splitter.split_documents(docs)
```

`BaseLoader`把数据加载成`Documents` object，存到 `Documents`类中的`page_content`中。

#### (3) Document基类

`Document`允许用户与文档的内容进行交互，可以查看文档内容。

```python
class Document(Serializable):
    """用于存储文本及其关联元数据的类。"""

    page_content: str
    """字符串文本。"""
    metadata: dict = Field(default_factory=dict)
    """关于页面内容的任意元数据（例如，来源、与其他文档的关系等）。"""
    type: Literal["Document"] = "Document"

    def __init__(self, page_content: str, **kwargs: Any) -> None:
        """将 page_content 作为位置参数或命名参数传入。"""
        super().__init__(page_content=page_content, **kwargs)

    @classmethod
    def is_lc_serializable(cls) -> bool:
        """返回此类是否可序列化。"""
        return True

    @classmethod
    def get_lc_namespace(cls) -> List[str]:
        """获取 langchain 对象的命名空间。"""
        return ["langchain", "schema", "document"]
```

通过 存 + 读的两个基类的抽象，满足不同类型加载器在数据形式上的统一。除此之外，其中的`metadata`会根据loader实现的不同写入不同的数据，同样是一个必要的基础属性。而不论任何基于LangChain实现的loader，搞明白这几点内容，再去理解和使用不同的文档加载器就会轻松很多，至此，大家也就能够理解为什么`PDFloader`和`TextLoader`都使用`load`去加载，且都使用`.page_content`和`.metadata`读取数据。

最后，我们需要特别关注JSON数据格式以及自定义JSON格式文档加载器的方法。在实际应用场景中，JSON格式的数据占有很大比例，而且其JSON的形式也是多样的，LangChain已经实现的JSON文档加载器并无法适用于所有数据形式，所以掌握如何自定义文档解析器，是重要且必要的。

### 3.5 加载JSON格式

#### (1) `jq`库

LangChain提供的JSON格式的文档加载器是`JSONLoader`，根据其说明，JSONLoader 使用指定的 jq 架构来解析 JSON文件，以便从输入的JSON中提取出想要加载的那部分

**介绍**

所谓的jq，它是一个轻量级的命令行 JSON 处理器，可以通过特定的语法在命令行中对 JSON 格式的数据进行各种复杂的处理，包括数据过滤、映射、减少和转换。jq 的语法设计得非常灵活和强大，使其成为处理 JSON 数据的首选工具之一。

它的主要特点包括：

1. `灵活的过滤器`：通过简单的过滤器表达式，可以轻松提取数据、修改数据结构或筛选出满足特定条件的数据项。
2. `无需循环`：与编写复杂的脚本或程序不同，jq 允许你直接应用表达式来处理数据，无需编写循环语句。
3. `多样的函数`：jq 提供了大量的内置函数，用于字符串处理、数值计算、数组/对象操作等，也支持自定义函数。
4. `管道操作`：jq 支持管道操作（类似于 UNIX/Linux 中的管道），可以将一个表达式的输出作为另一个表达式的输入，实现复杂的数据处理流程。

**例子**

比如jq 的一个基本示例是，我们可以使用它来提取 JSON 数据中的特定字段。假设有一个 JSON 文件 `example.json`，内容如下：

```json
{
  "employees": [
    {"name": "John", "age": 30, "city": "New York"},
    {"name": "Jane", "age": 25, "city": "Los Angeles"},
    {"name": "Doe", "age": 28, "city": "Chicago"}
  ]
}
```

可以使用 jq 的命令行工具来提取所有员工的名字，命令如下：

```bash
jq '.employees[].name' example.json
```

这条命令会输出：

```
"John"
"Jane"
"Doe"
```

**参考**

jq 的这些能力使其在数据处理和分析中非常有用，尤其是当处理复杂或大量的 JSON 数据时。更多的jq使用技巧，可以查阅：https://en.wikipedia.org/wiki/Jq_(programming_language)

**安装**

既然`JSONLoader`是使用jq来解析JSON文件，所以在使用前，就必须进行jq库的安装。

In [26]:
! pip install jq

Looking in indexes: http://mirrors.aliyun.com/pypi/simple
     |████████████████████████████████| 665 kB 1.9 MB/s eta 0:00:01


#### (2) JsonLoader支持的JSON格式

JSON有很多种存储的形式，当然对于提取信息的结构也会有很大的差别，LangChain实现的`JSONLoader`支持的JSON解析结构如下：

```python
class JSONLoader(BaseLoader):
    """Load a `JSON` file using a `jq` schema.

    Example:
        [{"text": ...}, {"text": ...}, {"text": ...}] -> schema = .[].text
        {"key": [{"text": ...}, {"text": ...}, {"text": ...}]} -> schema = .key[].text
        ["", "", ""] -> schema = .[]
    """
```

#### (3) 查看将要加载的数据

In [27]:
import json
from pathlib import Path
from pprint import pprint

file_path='./data/test.json'
data = json.loads(Path(file_path).read_text(encoding="utf-8"))

In [28]:
pprint(data)

[{'_id': '4759',
  'commentary': [["2'", '鲍里索夫球员Nikolai Signevich拼抢犯规,对手获得控球权.', '0-0'],
                 ["2'", '拉波尔特为毕尔巴鄂竞技在对方半场,赢得一个任意球.', '0-0'],
                 ["2'", '毕尔巴鄂竞技球员贝尼亚特大禁区外尝试左脚射门,可惜皮球稍稍偏出了右球门.', '0-0'],
                 ["4'", '鲍里索夫球员波利亚科夫拼抢犯规,对手获得控球权.', '0-0'],
                 ["4'", '阿杜里斯为毕尔巴鄂竞技在左路,赢得一个任意球.', '0-0'],
                 ["6'", 'Anri Khagush为鲍里索夫在右路,赢得一个任意球.', '0-0'],
                 ["6'", '毕尔巴鄂竞技球员拼抢犯规,对手获得控球权.', '0-0'],
                 ["7'", '鲍里索夫球员Nikolai Signevich拼抢犯规,对手获得控球权.', '0-0'],
                 ["7'", '伊莱索斯为毕尔巴鄂竞技赢得一个任意球.', '0-0'],
                 ["7'", '毕尔巴鄂竞技伊莱索斯受伤倒地,比赛暂停', '0-0'],
                 ["9'", '暂停结束,球员们重新开始比赛.', '0-0'],
                 ["9'", 'Anri Khagush为鲍里索夫赢得一个任意球.', '0-0'],
                 ["9'", '毕尔巴鄂竞技球员I-戈麦斯拼抢犯规,对手获得控球权.', '0-0'],
                 ["11'", '鲍里索夫球员Evgeni Yablonski拼抢犯规,对手获得控球权.', '0-0'],
                 ["11'", '穆尼亚因为毕尔巴鄂竞技赢得一个任意球.', '0-0'],
                 ["14'", '毕尔巴鄂竞技球员拉波尔特手球犯规,对手获得球权.', 

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



['拉科一次很好的进攻机会，禁区内左侧卢卡斯找到机会', "下半场15'", '0-4'],
                 ['卢卡斯凌空爆射，角度还是不够，被布拉沃倒地扑出来', "下半场16'", '0-4'],
                 ['边路争抢阿尔维斯犯规', "下半场16'", '0-4'],
                 ['西德内伊后场长传，右路刚刚上来的卡塔维亚得球', "下半场16'", '0-4'],
                 ['往中路走，再分边右路上来的劳雷', "下半场16'", '0-4'],
                 ['劳雷下底传中，巴尔特拉头球解围', "下半场16'", '0-4'],
                 ['拉科持续的进攻，直塞一个穿透球，找里埃拉', "下半场17'", '0-4'],
                 ['里埃拉右侧插上没有救下这个球，给大了', "下半场17'", '0-4'],
                 ['拉科现在防守也无所谓了，希望能够进一个，挽回颜面', "下半场17'", '0-4'],
                 ['巴萨外围的进攻，给到了拉基蒂奇脚下，对方逼抢不紧', "下半场18'", '0-4'],
                 ['拉基蒂奇抡一脚远射，高了', "下半场18'", '0-4'],
                 ['拉科很有意思，只防MSN，对别人不设防，基本只要不入禁区，随便', "下半场18'", '0-4'],
                 ['苏神大四喜了', "下半场19'", '0-5'],
                 ['刚刚哪位球迷预测的，苏神果然大四喜了，还有一个助攻呢', "下半场19'", '0-5'],
                 ['巴萨的过顶球送入禁区，拉科又是造越位失误，依然是劳雷拖在了最后，禁区内内马尔和苏神2打1',
                  "下半场20'",
                  '0-5'],
                 ['内马尔面对出击的曼努，横拨给另外一端的苏神，苏神推射被劳雷用身体挡出，第二下再射空门，想不进都

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



#### (4) 使用`JSONLoader`加载

In [29]:
from langchain_community.document_loaders import JSONLoader

jq 的查询语法是围绕管道操作符 | 来构建的，可以从JSON 结构中提取特定的信息，比如：

In [30]:
loader = JSONLoader(
    file_path='./data/test.json', 
    jq_schema='.[].commentary',
    text_content=False)

data = loader.load()

In [32]:
pprint(data[:1])

[Document(page_content='[["2\'", \'鲍里索夫球员Nikolai Signevich拼抢犯规,对手获得控球权.\', \'0-0\'], ["2\'", \'拉波尔特为毕尔巴鄂竞技在对方半场,赢得一个任意球.\', \'0-0\'], ["2\'", \'毕尔巴鄂竞技球员贝尼亚特大禁区外尝试左脚射门,可惜皮球稍稍偏出了右球门.\', \'0-0\'], ["4\'", \'鲍里索夫球员波利亚科夫拼抢犯规,对手获得控球权.\', \'0-0\'], ["4\'", \'阿杜里斯为毕尔巴鄂竞技在左路,赢得一个任意球.\', \'0-0\'], ["6\'", \'Anri Khagush为鲍里索夫在右路,赢得一个任意球.\', \'0-0\'], ["6\'", \'毕尔巴鄂竞技球员拼抢犯规,对手获得控球权.\', \'0-0\'], ["7\'", \'鲍里索夫球员Nikolai Signevich拼抢犯规,对手获得控球权.\', \'0-0\'], ["7\'", \'伊莱索斯为毕尔巴鄂竞技赢得一个任意球.\', \'0-0\'], ["7\'", \'毕尔巴鄂竞技伊莱索斯受伤倒地,比赛暂停\', \'0-0\'], ["9\'", \'暂停结束,球员们重新开始比赛.\', \'0-0\'], ["9\'", \'Anri Khagush为鲍里索夫赢得一个任意球.\', \'0-0\'], ["9\'", \'毕尔巴鄂竞技球员I-戈麦斯拼抢犯规,对手获得控球权.\', \'0-0\'], ["11\'", \'鲍里索夫球员Evgeni Yablonski拼抢犯规,对手获得控球权.\', \'0-0\'], ["11\'", \'穆尼亚因为毕尔巴鄂竞技赢得一个任意球.\', \'0-0\'], ["14\'", \'毕尔巴鄂竞技球员拉波尔特手球犯规,对手获得球权.\', \'0-0\'], ["14\'", \'鲍里索夫球员Aleksandr Karnitski大禁区外右脚射门,被防守球员封堵.\', \'0-0\'], ["15\'", \'伊劳拉将球处理出底线,鲍里索夫获得角球.\', \'0-0\'], ["18\'", \'I-戈麦斯将球处理出底线,鲍里索夫获得角球.\', \'0-0\'], ["19\'", \'进球啦！！！

### 3.6 自定义JSON文档加载器

#### (1) 介绍

JSON是一种重要的文件格式，如果LangChain提供的内置加载器不够用，则需要自己来实现一个。

其核心是实现一个BaseLoader子类，它能够创建Document对象，这个对象封装了

* 提取的文本 ( page_content )
* 元数据 —— 例如作者姓名或发布日期等。

而在随后的流程中，`Document` 对象会被

* 格式化为输入到 LLM 中的提示，允许 LLM 使用 `Document` 中的信息来生成期望的回应（例如，总结文档）
* 也可以索引到向量数据库中以供将来检索和使用

对于文档加载器必须实现的的抽象是：

| 组件           | 描述                                        | 中文描述                           |
| -------------- | ------------------------------------------ | --------------------------------- |
| Document       | Contains text and metadata                 | 包含文本和元数据                   |
| BaseLoader     | Use to convert raw data into Documents     | 用于将原始数据转换为文档           |

#### (2) 测试数据

这里我们使用一个新的不同JSON格式的数据集，这是一个哈利波特角色化对话数据集，为了研究如何在虚拟世界中构建角色化智能对话机器人，如智能游戏NPC等，数据存储为json形式。主要内容包括
- 对话所在位置（在书中的第几章节以及第几事件）
- 说话人
- 对话场景
- 对话内容
- 参与对话的角色属性
- 参与对话的角色与哈利的关系
- 答案正例（仅测试集）
- 答案负例（仅测试集）

数据样本见附带的压缩包中的“/data/cn_test_set.json“文件

#### (3) 代码实现

它的核心是load方法，用于返回Document对象，而parse方法使用了jq这个Lib

In [33]:
import json
from pathlib import Path
from typing import Any, Callable, Dict, List, Optional, Union

from langchain_core.documents import Document

from langchain_community.document_loaders.base import BaseLoader


class CustomJSONLoader(BaseLoader):
    """Load a `JSON` file using a `jq` schema.

    """

    def __init__(
        self,
        file_path: Union[str, Path],
        jq_schema: str,
    ):
        """Initialize the JSONLoader.

        参数:
            file_path (Union[str, Path]): JSON 或 JSON Lines 文件的路径。
            jq_schema (str): 用来从 JSON 中提取数据或文本的 jq 模式。

        """
        
        import jq
        
        self.file_path = Path(file_path).resolve()
        self._jq_schema = jq.compile(jq_schema)

    def load(self) -> List[Document]:
        """从 JSON 文件中加载并返回文档。"""
        docs: List[Document] = []
        self._parse(self.file_path.read_text(encoding="utf-8"), docs)
        return docs

    def _parse(self, content: str, docs: List[Document]) -> None:
        """将给定内容转换为文档。"""
        # content : 原始的JSON
        # json.loads(content)：JSON 格式的字符串 content 转换为 Python 的数据结构。具体转换为哪种形式的数据结构取决于原始 JSON 字符串的内容：
        
        # 根据jq编译查找到的结果
        data = self._jq_schema.input(json.loads(content)).all()
 
        for i, sample in enumerate(data, len(docs) + 1):
            metadata={"result": "\n".join(sample), "source": self.file_path}
            docs.append(Document(page_content="\n".join(sample), metadata=metadata))

#### (4) 测试

In [35]:
import json
from pathlib import Path
from pprint import pprint


loader = CustomJSONLoader(
    file_path='./data/cn_test_set.json', 
    jq_schema='."Session-3"."对话历史"',)

data = loader.load()

pprint(data)

[Document(page_content='哈利说：这是什么?\n佩妮说：你的新校服呀。\n哈利说：哦，我不知道还得泡得这么湿。\n佩妮说：别冒傻气，我把达力的旧衣服染好给你用。等我染好以后，穿起来就会跟别人的一模一样。', metadata={'result': '哈利说：这是什么?\n佩妮说：你的新校服呀。\n哈利说：哦，我不知道还得泡得这么湿。\n佩妮说：别冒傻气，我把达力的旧衣服染好给你用。等我染好以后，穿起来就会跟别人的一模一样。', 'source': PosixPath('/root/autodl-tmp/LangChain全面剖析/05 LangChain全面剖析之Retrieval/data/cn_test_set.json')})]


In [36]:
data[0].page_content

'哈利说：这是什么?\n佩妮说：你的新校服呀。\n哈利说：哦，我不知道还得泡得这么湿。\n佩妮说：别冒傻气，我把达力的旧衣服染好给你用。等我染好以后，穿起来就会跟别人的一模一样。'

In [37]:
data[0].metadata

{'result': '哈利说：这是什么?\n佩妮说：你的新校服呀。\n哈利说：哦，我不知道还得泡得这么湿。\n佩妮说：别冒傻气，我把达力的旧衣服染好给你用。等我染好以后，穿起来就会跟别人的一模一样。',
 'source': PosixPath('/root/autodl-tmp/LangChain全面剖析/05 LangChain全面剖析之Retrieval/data/cn_test_set.json')}

In [43]:
import json
from pathlib import Path
from pprint import pprint


loader = CustomJSONLoader(
    file_path='./data/cn_test_set.json', 
    jq_schema='."Session-1"."对话历史"',)

data = loader.load()

pprint(data)

[Document(page_content='佩妮说：坏消息，弗农，费格太太把腿摔断了，不能来接他了。现在怎么办?\n弗农说：咱们给玛姬挂个电话吧。\n佩妮说：别犯傻了，弗农，她讨厌这孩子。\n弗农说：她叫什么来着，你的那位朋友——伊芬，怎么样?\n佩妮说：上马约卡岛【在西地中海，属西班牙】度假去了。\n哈利说：你们可以把我留在家里。\n佩妮说：好让我们回来看到整个房子都给毁了?\n哈利说：我不会把房子炸掉的。\n佩妮说：我想我们可以带他到动物园去，然后把他留在车上……\n弗农说：那是辆新车，不能让他一个人待在车上……\n佩妮说：我的好心肝宝贝，别哭，妈妈不会让他搅乱你的好日子的!\n达力说：我……不……想让……他……去……去!他总是把什么都弄坏了!\n佩妮说：哎呀，天哪，他们来了!\n弗农说：我现在警告你，小子，只要你干出一点点蠢事——干出任何事——那你就在你的碗柜里待着，等圣诞节再出来吧。', metadata={'result': '佩妮说：坏消息，弗农，费格太太把腿摔断了，不能来接他了。现在怎么办?\n弗农说：咱们给玛姬挂个电话吧。\n佩妮说：别犯傻了，弗农，她讨厌这孩子。\n弗农说：她叫什么来着，你的那位朋友——伊芬，怎么样?\n佩妮说：上马约卡岛【在西地中海，属西班牙】度假去了。\n哈利说：你们可以把我留在家里。\n佩妮说：好让我们回来看到整个房子都给毁了?\n哈利说：我不会把房子炸掉的。\n佩妮说：我想我们可以带他到动物园去，然后把他留在车上……\n弗农说：那是辆新车，不能让他一个人待在车上……\n佩妮说：我的好心肝宝贝，别哭，妈妈不会让他搅乱你的好日子的!\n达力说：我……不……想让……他……去……去!他总是把什么都弄坏了!\n佩妮说：哎呀，天哪，他们来了!\n弗农说：我现在警告你，小子，只要你干出一点点蠢事——干出任何事——那你就在你的碗柜里待着，等圣诞节再出来吧。', 'source': PosixPath('/root/autodl-tmp/LangChain全面剖析/05 LangChain全面剖析之Retrieval/data/cn_test_set.json')})]


In [45]:
import json
from pathlib import Path
from pprint import pprint

# 假设你已经知道有多少个 Session 或者你可以动态地获取到 Session 的总数
total_sessions = 3  # 示例中假设有 3 个 Session

for i in range(1, total_sessions + 1):
    jq_schema = f'."Session-{i}"."对话历史"'
    
    # 为每个 Session 重新实例化 loader
    loader = CustomJSONLoader(
        file_path='./data/cn_test_set.json', 
        jq_schema=jq_schema,
    )
    
    # 加载数据
    data = loader.load()
    
    # 打印或处理数据
    pprint(data)
    # 你可以在这里做进一步的数据处理

[Document(page_content='佩妮说：坏消息，弗农，费格太太把腿摔断了，不能来接他了。现在怎么办?\n弗农说：咱们给玛姬挂个电话吧。\n佩妮说：别犯傻了，弗农，她讨厌这孩子。\n弗农说：她叫什么来着，你的那位朋友——伊芬，怎么样?\n佩妮说：上马约卡岛【在西地中海，属西班牙】度假去了。\n哈利说：你们可以把我留在家里。\n佩妮说：好让我们回来看到整个房子都给毁了?\n哈利说：我不会把房子炸掉的。\n佩妮说：我想我们可以带他到动物园去，然后把他留在车上……\n弗农说：那是辆新车，不能让他一个人待在车上……\n佩妮说：我的好心肝宝贝，别哭，妈妈不会让他搅乱你的好日子的!\n达力说：我……不……想让……他……去……去!他总是把什么都弄坏了!\n佩妮说：哎呀，天哪，他们来了!\n弗农说：我现在警告你，小子，只要你干出一点点蠢事——干出任何事——那你就在你的碗柜里待着，等圣诞节再出来吧。', metadata={'result': '佩妮说：坏消息，弗农，费格太太把腿摔断了，不能来接他了。现在怎么办?\n弗农说：咱们给玛姬挂个电话吧。\n佩妮说：别犯傻了，弗农，她讨厌这孩子。\n弗农说：她叫什么来着，你的那位朋友——伊芬，怎么样?\n佩妮说：上马约卡岛【在西地中海，属西班牙】度假去了。\n哈利说：你们可以把我留在家里。\n佩妮说：好让我们回来看到整个房子都给毁了?\n哈利说：我不会把房子炸掉的。\n佩妮说：我想我们可以带他到动物园去，然后把他留在车上……\n弗农说：那是辆新车，不能让他一个人待在车上……\n佩妮说：我的好心肝宝贝，别哭，妈妈不会让他搅乱你的好日子的!\n达力说：我……不……想让……他……去……去!他总是把什么都弄坏了!\n佩妮说：哎呀，天哪，他们来了!\n弗农说：我现在警告你，小子，只要你干出一点点蠢事——干出任何事——那你就在你的碗柜里待着，等圣诞节再出来吧。', 'source': PosixPath('/root/autodl-tmp/LangChain全面剖析/05 LangChain全面剖析之Retrieval/data/cn_test_set.json')})]
[Document(page_content='达力说：让它动呀。\n巨蟒说：我总是碰到像他们这样的人。\n哈利说：我知道。别的不说，你是从哪里来的?那边不错吧?哦，我明

&emsp;&emsp;整体看，在LangChain的抽象下去接入一个自定义的文档加载器是不复杂的，虽然我们仅仅是通过一个较为简单和基础的示例来向大家展示构建自定义文档加载器的流程，但只要覆盖到其核心的过程，需要修改的就只是具体情境下数据的处理逻辑。这包括继承自`BaseLoader`基类，将内容写入`Document`对象中的`page_content`，并重新定义`metadata`。

## 4. Document Transformer

### 4.1 功能介绍

&emsp;&emsp;Transformer用来对文本进行切块

&emsp;&emsp;当使用LangChain应用框架实现这个流程时，`Knowledge`到`raw data`的转换实际上就是由`Document loaders`组件来完成的。该组件将不同来源的数据源均转化为`Document`对象。无论是常见的文件格式（如.txt或.json），还是各种不同的数据（如GitHub或MongoDB），`Document loaders`都能将这些数据统一处理，形成标准化的`Document`对象，以便进行后续的处理步骤。

&emsp;&emsp;当拿到统一的一个`Document`对话后，接下来其实就是需要把每一个`raw data`都切分成Chunks，而关于为什么要切分成Chunks的原因参考前面RAG构建流程的的介绍，因为本质上RAG是一种将通过某种手段信息得到的检索信息先插入大模型提示中，再送入模型的的过程，所以通过RAG检索到的这部分内容，如果是作为一个整体的`Document`对象，那么会存在两点问题：

1. 假设提问的Query的答案出现在某一个`Document`对象中，那么将检索到的整个`Document`对象直接放入`Prompt`中并不是最优的选择，因为其中一定会包含非常多无关的信息，而无效信息越多，对大模型后续的推理影响越大。

2. 任何一个大模型都存在最大输入的Token限制，如果一个`Document`非常大，比如一个几百兆的PDF，那么肯定无法容纳如此多的信息。

&emsp;&emsp;所以针对上述两个问题，提出的一个有效的解决方案就是将完整的`Document`对象进行分块处理（Chunking）。无论是在存储还是检索过程中，都将以这些块（chunks）为基本单位，从而有效地避免内容不相关性问题和超出最大输入限制的问题。分块（Chunking）是指将文本切分为更小的部分的过程，虽然这听起来简单，但实际操作中需要处理许多细节问题。不同类型的文本通常需要采用不同的分块策略。在构建检索增强型生成（RAG）应用程序的整个流程中，分块是最具挑战性的环节之一，它显著影响检索效果。目前还没有通用的方法可以明确指出哪一种分块策略最为有效。不同的使用场景和数据类型都会影响分块策略的选择。

&emsp;&emsp;Chunking环节对RAG的效果至关重要

### 4.2 Chunking拆分策略

#### (1) 介绍

Langchain提供了很多种拆分策略：[https://python.langchain.com/v0.1/docs/modules/data_connection/document_transformers/](https://python.langchain.com/v0.1/docs/modules/data_connection/document_transformers/)

下面列出5种，其中第四种普世性比较好

1. **根据句子切分**：这种方法按照自然句子边界进行切分，以保持语义完整性。
2. **按照固定字符数来切分**：这种策略根据特定的字符数量来划分文本，但可能会在不适当的位置切断句子。
3. **按固定字符数来切分，结合重叠窗口（overlapping windows）**：此方法与按字符数切分相似，但通过重叠窗口技术避免切分关键内容，确保信息连贯性。
4. **递归方法**：通过递归方式动态确定切分点，这种方法可以根据文档的复杂性和内容密度来调整块的大小。
5. **根据语义切割**：这种高级策略依据文本的语义内容来划分块，旨在保持相关信息的集中和完整，适用于需要高度语义保持的应用场景。

第二种方法（按照字符数切分）和第三种方法（按固定字符数切分结合重叠窗口）主要基于字符进行文本的切分，而不考虑文章的实际内容和语义。这种方式虽简单，但可能会导致主题或语义上的断裂。相对而言，递归方法更加灵活和高效，它结合了固定长度切分和语义分析。通常是首选策略，因为它能够更好地确保每个段落包含一个完整的主题。而最后一项，基于语义的分割虽然能精确地切分出完整的主题段落，但这种方法效率较低。它需要运行复杂的分段算法（segmentation algorithm），处理速度较慢，并且段落长度可能极不均匀——有的主题段落可能很长，而有的则较短。因此，尽管它在某些需要高精度语义保持的场景下有其应用价值，但并不适合所有情况。

这些方法各有优势和局限，选择适当的分块策略取决于具体的应用需求和预期的检索效果。接下来我们依次尝试用常规手段应该如何实现上述几种方法的文本切分。

#### (2) 根据句子切分（原理演示）

按照句子切分，其实就是通过标点符号来进行文本切分（分割），这可以直接使用Python的标准库来完成这个任务。一种简单的方法是使用re模块，它提供了正则表达式的支持，可以方便地根据标点符号来分割文本。如下示例中，展示了如何使用re.split()函数来根据中文和英文的标点符号进行文本切分。代码如下：

In [47]:
import re

def split_text_by_punctuation(text):
    # 定义一个正则表达式，包括常见的中英文标点
    # pattern = r"[。！？｡＂＃＄％＆＇（）＊＋，－／：；＜＝＞＠［＼］＾＿｀｛｜｝～\s、]+"
    pattern = r"[。！？｡]+"
    # 使用正则表达式进行分割
    segments = re.split(pattern, text)
    # 过滤掉空字符串
    return [segment for segment in segments if segment]

这个函数会根据中文和英文的标点符号来分割文本，并移除空字符串。定义好分割函数后，我们可以尝试进行功能测试：

In [48]:
# 文本
text = "盼望着，盼望着，东风来了，春天的脚步近了。\
一切都象刚睡醒的样子，欣欣然张开了眼。山朗润起来了，水涨起来了，太阳的脸红起来了！\
小草偷偷地从土里钻出来，嫩嫩的，绿绿的。园子里，田野里，瞧去，一大片一大片满是的。\
坐着，趟着，打两个滚，踢几脚球，赛几趟跑，捉几回迷藏。风轻悄悄的，草软绵绵的。"

# 调用函数进行分割
segments = split_text_by_punctuation(text)

# 使用循环来打印每个chunk
for i, segment in enumerate(segments):
    print("Chunk {}: {}".format(i + 1, segment))

Chunk 1: 盼望着，盼望着，东风来了，春天的脚步近了
Chunk 2: 一切都象刚睡醒的样子，欣欣然张开了眼
Chunk 3: 山朗润起来了，水涨起来了，太阳的脸红起来了
Chunk 4: 小草偷偷地从土里钻出来，嫩嫩的，绿绿的
Chunk 5: 园子里，田野里，瞧去，一大片一大片满是的
Chunk 6: 坐着，趟着，打两个滚，踢几脚球，赛几趟跑，捉几回迷藏
Chunk 7: 风轻悄悄的，草软绵绵的


如上所示，一整段`text`会根据设定的标点符号被分割为多个`chunks`，当然如果有特定的分割需求（比如保留某些特定的标点符号），可以调整正则表达式来灵活的调整。

缺点是切分的比较碎

#### (3) 根据固定字符数切分（原理演示）

如果想按照固定字符数来切分文本，这种方法就不再依赖于标点符号，而是简单地按照给定的字符数来切分文本。我们可以编写一个函数，用来将文本分割成指定长度的片段。代码如下：

In [51]:
def split_text_by_fixed_length(text, length):
    # 使用列表推导式按固定长度切分文本
    return [text[i:i + length] for i in range(0, len(text), length)]

这个函数的作用是根据指定的长度（在这个例子中为60个字符）来切分文本。我们可以根据具体需要调整这个长度。

In [52]:
# 文本
text = "盼望着，盼望着，东风来了，春天的脚步近了。\
一切都象刚睡醒的样子，欣欣然张开了眼。山朗润起来了，水涨起来了，太阳的脸红起来了！\
小草偷偷地从土里钻出来，嫩嫩的，绿绿的。园子里，田野里，瞧去，一大片一大片满是的。\
坐着，趟着，打两个滚，踢几脚球，赛几趟跑，捉几回迷藏。风轻悄悄的，草软绵绵的。"

# 定义每个片段的长度
chunk_length = 60

# 调用函数进行分割
result = split_text_by_fixed_length(text, chunk_length)

# 打印结果
for i, segment in enumerate(result):
    print(f"Chunk {i+1}: {segment}")

Chunk 1: 盼望着，盼望着，东风来了，春天的脚步近了。一切都象刚睡醒的样子，欣欣然张开了眼。山朗润起来了，水涨起来了，太阳的脸红起来
Chunk 2: 了！小草偷偷地从土里钻出来，嫩嫩的，绿绿的。园子里，田野里，瞧去，一大片一大片满是的。坐着，趟着，打两个滚，踢几脚球，赛
Chunk 3: 几趟跑，捉几回迷藏。风轻悄悄的，草软绵绵的。


然而，这种方法的一个明显缺点是由于仅依据长度进行切分，切分后的片段可能无法保持完整的语义。但并不意味着它不适用于文本切分任务。例如，这种方法非常适合于处理日志文件或代码块，其中文本通常以固定长度或格式出现，或者在处理来自传感器或其他实时数据源的流数据时，固定长度切分可以确保数据被均匀地处理和分析。这些应用场景中，数据的结构和形式通常是预定和规范的，因此即便是按固定长度进行切分，反而会更有利于对数据的理解和使用。

#### (4) 结合重叠窗口的固定字符数切分（原理演示）

重复窗口的意义是：块之间保持一些重叠，以确保语义上下文不会在块之间丢失。在文本处理和其他数据分析领域，"重叠"（overlap）指的是连续数据块之间共享的部分。这种方法特别常见于信号处理、语音分析、自然语言处理等领域，其中数据的连续性和上下文信息非常重要。比如下述代码所示：

In [53]:
def split_text_by_fixed_length_with_overlap(text, length, overlap):
    # 使用列表推导式按固定长度及重叠长度切分文本
    return [text[i:i + length] for i in range(0, len(text) - overlap, length - overlap)]

In [54]:
# 文本
text = "盼望着，盼望着，东风来了，春天的脚步近了。\
一切都象刚睡醒的样子，欣欣然张开了眼。山朗润起来了，水涨起来了，太阳的脸红起来了！\
小草偷偷地从土里钻出来，嫩嫩的，绿绿的。园子里，田野里，瞧去，一大片一大片满是的。\
坐着，趟着，打两个滚，踢几脚球，赛几趟跑，捉几回迷藏。风轻悄悄的，草软绵绵的。"

# 定义每个片段的长度和重叠长度
chunk_length = 60
overlap_length = 20

# 调用函数进行分割
result = split_text_by_fixed_length_with_overlap(text, chunk_length, overlap_length)

# 打印结果
for i, segment in enumerate(result):
    print(f"Chunk {i+1}: {segment}")

Chunk 1: 盼望着，盼望着，东风来了，春天的脚步近了。一切都象刚睡醒的样子，欣欣然张开了眼。山朗润起来了，水涨起来了，太阳的脸红起来
Chunk 2: 山朗润起来了，水涨起来了，太阳的脸红起来了！小草偷偷地从土里钻出来，嫩嫩的，绿绿的。园子里，田野里，瞧去，一大片一大片满
Chunk 3: 的。园子里，田野里，瞧去，一大片一大片满是的。坐着，趟着，打两个滚，踢几脚球，赛几趟跑，捉几回迷藏。风轻悄悄的，草软绵绵
Chunk 4: 几趟跑，捉几回迷藏。风轻悄悄的，草软绵绵的。


### 4.3 LangChain提供的可视化工具

&emsp;&emsp;在上一小节的三种切分方法下，虽然简单且更容易理解，但其存在的核心问题是：完全忽视了文档的结构，只是单纯按固定字符数量进行切分。所以难免要更进一步地去做优化，那么一个更进阶的文本分割器应该具备的是：

- 能够将文本分成小的、具有语义意义的块（通常是句子）。
- 可以通过某些测量方法，将这些小块组合成一个更大的块，直到达到一定的大小。
- 一旦达到该大小，请将该块设为自己的文本片段，然后创建具有一些重叠的新文本块，以保持块之间的上下文。

&emsp;&emsp;根据上述需求，衍生出来的就是递归字符文本切分器，在langChain中的抽象类为：`RecursiveCharacterTextSplitter`，同时它也是Langchain的默认文本分割器，在`Baseloader`类中，其数据加载和切分代码如下所示：

```python
class BaseLoader(ABC):
    
    def load(self) -> List[Document]:
        """Load data into Document objects."""
        return list(self.lazy_load())
    
    def load_and_split(
        self, text_splitter: Optional[TextSplitter] = None
    ) -> List[Document]:
        """Load Documents and split into chunks. Chunks are returned as Documents.

        Do not override this method. It should be considered to be deprecated!

        Args:
            text_splitter: TextSplitter instance to use for splitting documents.
              Defaults to RecursiveCharacterTextSplitter.

        Returns:
            List of Documents.
        """

        if text_splitter is None:
            try:
                from langchain_text_splitters import RecursiveCharacterTextSplitter
            except ImportError as e:
                raise ImportError(
                    "Unable to import from langchain_text_splitters. Please specify "
                    "text_splitter or install langchain_text_splitters with "
                    "`pip install -U langchain-text-splitters`."
                ) from e

            _text_splitter: TextSplitter = RecursiveCharacterTextSplitter()
        else:
            _text_splitter = text_splitter
        docs = self.load()
        return _text_splitter.split_documents(docs)
    
    .......
    .......
```

&emsp;&emsp;我们可以用LangChain提供的文本切分可视化小工具进行直观的理解：https://langchain-text-splitter.streamlit.app/

&emsp;&emsp;如上代码所展示的就是`RecursiveCharacterTextSplitter`类的核心逻辑。所谓的按字符递归分割，就是使用一组分隔符以分层和迭代的方式将输入文本分成更小的块。默认使用[“\n\n” ,"\n" ," ",""] 这四个特殊符号作为分割文本的标记，如果分割文本开始的时候没有产生所需大小或结构的块，那么这个方法会使用不同的分隔符或标准对生成的块递归调用，直到获得所需的块大小或结构。这意味着虽然这些块的大小并不完全相同，但它们仍然会逼近差不多的大小。其中的关键参数：
- separators：指定分割文本的分隔符
- chunk_size：被切割字符的最大长度
- chunk_overlap：如果仅仅使用chunk_size来切割时，前后两段字符串重叠的字符数量。
- length_function:如何计算块的长度。默认情况下，只计算字符数，也可以选择按照Token。

超出Chunk Size只是触发条件，而能不能分割，取决于`separator`设置的关键词。

&emsp;&emsp;当然，除了按照 `length_function = len`（即字符长度）来进行切分，也可以按照Token切分，Token和字符大概是1 ：4 这样一个比例，原理是一致的.

&emsp;&emsp;除了上面文本切分的可视化工具可供我们测试使用外，LangChain还推荐了一个文本可视化工具ChunkViz，大家也可自行尝试，其访问地址：https://chunkviz.up.railway.app/

### 4.7 LangChain提供的切分器

#### (1) 要实现的接口

```python
class TextSplitter(BaseDocumentTransformer, ABC):
    """用于将文本分割成块的接口。"""

    def __init__(
        self,
        chunk_size: int = 4000,
        chunk_overlap: int = 200,
        length_function: Callable[[str], int] = len,
        keep_separator: bool = False,
        add_start_index: bool = False,
        strip_whitespace: bool = True,
    ) -> None:
        """
        创建一个新的文本分割器。

        参数：
            chunk_size: 返回块的最大尺寸
            chunk_overlap: 块之间的字符重叠
            length_function: 用于测量给定块长度的函数
            keep_separator: 是否在块中保留分隔符
            add_start_index: 如果为 `True`，则在元数据中包含块的起始索引
            strip_whitespace: 如果为 `True`，则从每个文档的开始和结束处去除空白字符
        """
        if chunk_overlap > chunk_size:
            raise ValueError(
                f"重叠大小（{chunk_overlap}）大于块大小（{chunk_size}），应该更小。"
            )

    @abstractmethod
    def split_text(self, text: str) -> List[str]:
        """将文本分割成多个组件。"""

    def create_documents(
        self, texts: List[str], metadatas: Optional[List[dict]] = None
    ) -> List[Document]:
        """从文本列表创建文档，其作用是将普通的文件对象转化成Document对象"""

    def split_documents(self, documents: Iterable[Document]) -> List[Document]:
        """分割文档。"""

    @classmethod
    def from_huggingface_tokenizer(cls, tokenizer: Any, **kwargs: Any) -> TextSplitter:
        """使用 HuggingFace 的分词器创建基于字符计数的文本分割器。"""

    @classmethod
    def from_tiktoken_encoder(
        cls: Type[TS],
        encoding_name: str = "gpt2",
        model_name: Optional[str] = None,
        allowed_special: Union[Literal["all"], AbstractSet[str]] = set(),
        disallowed_special: Union[Literal["all"], Collection[str]] = "all",
        **kwargs: Any,
    ) -> TS:
        """从 TikToken 编码器创建一个文本分割器，可以设置允许和禁止的特殊字符。"""


    def transform_documents(
        self, documents: Sequence[Document], **kwargs: Any
    ) -> Sequence[Document]:
        """通过分割它们来转换文档序列。"""
        return self.split_documents(list(documents))
            
```

| 方法名                           | 描述                                             |
|---------------------------------|-------------------------------------------------|
| `__init__([chunk_size, chunk_overlap, ...])` | 创建一个新的文本分割器。                           |
| `create_documents(texts[, metadatas])`       | 从文本列表创建文档。                               |
| `from_huggingface_tokenizer(tokenizer, **kwargs)` | 使用 HuggingFace 的分词器来计数长度的文本分割器。    |
| `from_tiktoken_encoder([encoding_name, ...])` | 使用 TikToken 编码器来计数长度的文本分割器。       |
| `split_documents(documents)`                 | 分割文档。                                         |
| `split_text(text)`                          | 将文本分割成多个组件。                             |
| `transform_documents(documents, **kwargs)`  | 通过分割它们来转换文档序列。                       |


#### (2) 递归切割：RecursiveCharacterTextSplitter

&emsp;&emsp;该文本分割器接受一个字符列表作为参数，根据第一个字符进行切块，但如果任何切块太大，则会继续移动到下一个字符，并以此类推。默认情况下，它尝试进行切割的字符包括 `["\n\n", "\n", " ", ""]`

&emsp;&emsp;除此之外，还可以指定的参数包括：

- length_function：用于计算切块长度的方法。默认只计算字符数，但通常这里会使用Token。
- chunk_size：切块的最大大小（由长度函数测量）。
- chunk_overlap：切块之间的最大重叠部分。保持一定程度的重叠可以使得各个切块之间保持连贯性（例如滑动窗口）。
- add_start_index：是否在元数据中包含每个切块在原始文档中的起始位置。

In [108]:
from langchain.text_splitter import RecursiveCharacterTextSplitter

In [109]:
text_splitter = RecursiveCharacterTextSplitter(
    separators=["\n\n", "\n", " ", ""], # 默认
    chunk_size=100, #块长度
    chunk_overlap=20, #重叠字符串长度
    add_start_index=True
)

读取两个原始文本。

In [112]:
# This is a long document we can split up.
with open("./data/langchain.txt", encoding="utf-8") as f:
    langchain_desc = f.read()

# This is a long document we can split up.
with open("./data/春.txt", encoding="utf-8") as f:
    chun_desc = f.read()

In [113]:
metadatas = [{"document": 1}, {"document": 2}]

In [114]:
text_res = text_splitter.create_documents(
    [langchain_desc, chun_desc], 
    metadatas=metadatas
)

In [115]:
len(text_res)

10

In [116]:
text_res[0]

Document(page_content='LangChain 是一个用于开发由大型语言模型 (LLMs) 驱动的应用程序的框架。LangChain简化了LLM应用程序生命周期的每个阶段。', metadata={'document': 1, 'start_index': 0})

In [117]:
text_res[1]

Document(page_content='LangChain 已经成为了我们每一个大模型开发工程师的标配。\n为什么要用 Langchain？', metadata={'document': 1, 'start_index': 73})

#### (3) 按照Token切分

&emsp;&emsp;大语言模型通常都有一个最大的输入Token限制。因此，当我们将文本拆分为块时，除了字符以外，更常用的一种方法计算Token的数量。所谓token可以理解为含义简单的最小词语单位，一个token大约由4个字符组成。这里提供一个Token与字符转化的可视化工具，有OpenAI提供：https://platform.openai.com/tokenizer

&emsp;&emsp;按照Token切分，采用的是一种字节对的编码（Byte Pair Encoder，BPE）方法，其内部的执行逻辑会使用到tiktoken库，它是由 OpenAI 创建的快速 BPE 分词器。因为大语言模型(LLM)通常是以token的数量作为其计量(或收费)的依据，所以采用token分割也有助于我们在使用时更好的控制成本。

In [ ]:
# ! pip install --upgrade --quiet langchain-text-splitters tiktoken

In [118]:
# This is a long document we can split up.
with open("./data/langchain.txt", encoding="utf-8") as f:
    langchain_desc = f.read()

&emsp;&emsp;`.from_tiktoken_encoder()` 方法采用 encoding 作为参数（例如 `cl100k_base` ，GPT系列模型采用的编码方式），或 model_name （例如 gpt-4 ）。 而`chunk_size` 、 `chunk_overlap` 和 `separators` 等所有附加参数都用于实例化：

In [119]:
text_splitter = CharacterTextSplitter.from_tiktoken_encoder(
    model_name="gpt-4", 
    chunk_size=100,
    chunk_overlap=0
)
texts = text_splitter.split_text(langchain_desc)

Created a chunk of size 411, which is longer than the specified 100


In [120]:
len(texts)

1

In [121]:
from langchain_text_splitters import RecursiveCharacterTextSplitter

In [122]:
text_splitter = RecursiveCharacterTextSplitter.from_tiktoken_encoder(
    model_name="gpt-4",
    chunk_size=100, #块长度
    chunk_overlap=0, #重叠字符串长度

)

In [123]:
texts = text_splitter.split_text(langchain_desc)
print(texts[0])

LangChain 是一个用于开发由大型语言模型 (LLMs) 驱动的应用程序的框架。LangChain简化了LLM应用程序生命周期的每个阶段。
LangChain 已经成为了我们每一个大模型开发工程师的标配。
为什么要用 Langchain？


In [124]:
len(texts)

7

In [125]:
import tiktoken

# 两种方式的结果一致
encoding = tiktoken.get_encoding("cl100k_base")
encoding = tiktoken.encoding_for_model("gpt-4")

encoding = tiktoken.get_encoding("cl100k_base")
print(encoding.encode("你好呀"))

[57668, 53901, 17857, 222]


In [126]:
print(encoding.decode([57668, 53901, 17857, 222]))

你好呀


In [127]:
text_splitter = RecursiveCharacterTextSplitter.from_tiktoken_encoder(
    encoding_name="cl100k_base", chunk_size=100, chunk_overlap=0
)
texts = text_splitter.split_text(langchain_desc)

In [128]:
print(texts[1])

数据连接：Langchain 允许你将大型语言模型连接到你自己的数据源，比如数据库、PDF文件或其他文档。这意味着你可以使模型从你的私有数据中提取信息。


In [129]:
len(texts)

7

#### (4) 特定数据类型 & 语言的文档切分方法

In [130]:
from langchain.text_splitter import MarkdownTextSplitter

In [131]:
markdown_text = """
# 主题：技术探讨

## 第一部分：前言

这是前言部分，简短介绍文档主旨。

## 第二部分：技术分析

### Python编程

### 解释

1. **标题**：使用不同级别的标题（从`#`到`###`）来组织文档结构。
2. **代码块**：分别用Python和JavaScript代码块来示例如何在Markdown中嵌入代码。
3. **水平线**：使用`***`和`---`创建水平线，用于文档中不同部分之间的视觉分隔。
"""

In [132]:
splitter = MarkdownTextSplitter(chunk_size = 60, chunk_overlap=10)

In [133]:
mardown_split = splitter.create_documents([markdown_text])

In [134]:
len(mardown_split)

5

&emsp;&emsp;同时，LangChain封装的`MarkdownHeaderTextSplitter`，它的切分逻辑是基于指定的标题来分割`markdown`文件。因为`Markdown`格式有特定的语法，一般整体内容由`h1、h2、h3`等多级标题组织，所以`MarkdownHeaderTextSplitter`得切分策略就是根据标题来分割文本内容。

In [ ]:
# ! pip install -qU langchain-text-splitters

In [135]:
markdown_text = """
# 主题：技术探讨

## 第一部分：前言

这是前言部分，简短介绍文档主旨。

## 第二部分：技术分析

### Python编程

### 解释
 
1. **标题**：使用不同级别的标题（从`#`到`###`）来组织文档结构。
2. **代码块**：分别用Python和JavaScript代码块来示例如何在Markdown中嵌入代码。
3. **水平线**：使用`***`和`---`创建水平线，用于文档中不同部分之间的视觉分隔。
"""

In [136]:
from langchain_text_splitters import MarkdownHeaderTextSplitter

headers_to_split_on = [
    ("#", "Header 1"),
    ("##", "Header 2"),
    ("###", "Header 3"),
]

markdown_splitter = MarkdownHeaderTextSplitter(headers_to_split_on=headers_to_split_on)
md_header_splits = markdown_splitter.split_text(markdown_text)

In [137]:
print(md_header_splits)

[Document(page_content='这是前言部分，简短介绍文档主旨。', metadata={'Header 1': '主题：技术探讨', 'Header 2': '第一部分：前言'}), Document(page_content='1. **标题**：使用不同级别的标题（从`#`到`###`）来组织文档结构。\n2. **代码块**：分别用Python和JavaScript代码块来示例如何在Markdown中嵌入代码。\n3. **水平线**：使用`***`和`---`创建水平线，用于文档中不同部分之间的视觉分隔。', metadata={'Header 1': '主题：技术探讨', 'Header 2': '第二部分：技术分析', 'Header 3': '解释'})]


&emsp;&emsp;除此之外，还有一个`CodeTextSplitter`,可以按照代码进行分割，支持代码的语言包括['cpp', 'go', 'java', 'js', 'php', 'proto', 'python', 'rst', 'ruby', 'rust', 'scala', 'swift', 'markdown', 'latex', 'html', 'sol']，比如Markdown(来源于`RecursiveCharacterTextSplitter`的`get_separators_for_language`方法)：
```python
        elif language == Language.MARKDOWN:
            return [
                # First, try to split along Markdown headings (starting with level 2)
                "\n#{1,6} ",   #  根据标题（H1 到 H6）来分割
                # Note the alternative syntax for headings (below) is not handled here
                # Heading level 2
                # ---------------
                # End of code block
                "```\n",      # 代码块
                # Horizontal lines   
                "\n\\*\\*\\*+\n",   # 水平线
                "\n---+\n",
                "\n___+\n",
                # Note that this splitter doesn't handle horizontal lines defined
                # by *three or more* of ***, ---, or ___, but this is not handled
                "\n\n",
                "\n",
                " ",   # 空格
                "",    # 字符
            ]
```

In [138]:
from langchain.text_splitter import (
    RecursiveCharacterTextSplitter,
    Language,
)

In [139]:
md_splitter = RecursiveCharacterTextSplitter.from_language(
    language=Language.MARKDOWN, chunk_size=60, chunk_overlap=0
)
md_docs = md_splitter.create_documents([markdown_text])
md_docs

[Document(page_content='# 主题：技术探讨\n\n## 第一部分：前言\n\n这是前言部分，简短介绍文档主旨。\n\n## 第二部分：技术分析'),
 Document(page_content='### Python编程'),
 Document(page_content='### 解释\n \n1. **标题**：使用不同级别的标题（从`#`到`###`）来组织文档结构。'),
 Document(page_content='2. **代码块**：分别用Python和JavaScript代码块来示例如何在Markdown中嵌入代码。'),
 Document(page_content='3. **水平线**：使用`***`和`---`创建水平线，用于文档中不同部分之间的视觉分隔。')]

## 5. Text Embedding Models

### 5.1 支持的Model

[https://python.langchain.com/v0.1/docs/integrations/text_embedding/](https://python.langchain.com/v0.1/docs/integrations/text_embedding/) 

[https://python.langchain.com/v0.2/docs/integrations/text_embedding/](https://python.langchain.com/v0.2/docs/integrations/text_embedding/)

### 5.2 代码演示

In [1]:
from langchain_openai import OpenAIEmbeddings
import openai,os

In [16]:
openai.api_key = os.getenv("OPENAI_API_KEY")
openai.api_base="https://api.openai.com/v1"
embeddings_model = OpenAIEmbeddings(model="text-embedding-ada-002",openai_api_key=openai.api_key ,openai_api_base=openai.api_base)

In [3]:
embeddings = embeddings_model.embed_documents(
    [
        "Hi there!",
        "Oh, hello!",
        "What's your name?",
        "My friends call me World",
        "Hello World!"
    ]
)
len(embeddings), len(embeddings[0])

(5, 1536)

In [4]:
embedded_query = embeddings_model.embed_query("What was the name mentioned in the conversation?")
embedded_query[:5]

[0.005384807424727807,
 -0.0005522561790177147,
 0.03896066510130955,
 -0.002939867294003909,
 -0.008987877434176603]

## 6. Vector Store

### 6.1 文档：Vector Store列表及例子

存储和搜索非结构化数据的最常见方法之一是嵌入它并存储生成的嵌入向量，然后在查询时嵌入非结构化查询并检索与嵌入查询“最相似”的嵌入向量。矢量存储负责存储嵌入数据并为您执行矢量搜索。

向量数据库列表：

[https://python.langchain.com/v0.2/docs/integrations/vectorstores/](https://python.langchain.com/v0.2/docs/integrations/vectorstores/) 

[https://python.langchain.com/v0.1/docs/integrations/vectorstores/](https://python.langchain.com/v0.1/docs/integrations/vectorstores/)

参考: 以Chroma为例，在上面的列表页面中找到这个向量数据库，点击打开网页后，就能看到参考代码

[https://python.langchain.com/v0.1/docs/integrations/vectorstores/chroma/](https://python.langchain.com/v0.1/docs/integrations/vectorstores/chroma/)

### 6.2 例子

以Chroma为例，其它向量数据库差别也不大

导入依赖

In [11]:
# import
from langchain_chroma import Chroma
from langchain_community.document_loaders import TextLoader
from langchain_community.embeddings.sentence_transformer import (
    SentenceTransformerEmbeddings,
)
from langchain_text_splitters import CharacterTextSplitter

初始化embedding Model

In [12]:
import openai
from langchain_openai import OpenAIEmbeddings

openai.api_key = os.getenv("OPENAI_API_KEY")
openai.api_base="https://api.openai.com/v1"
# 将分割后的文本，使用 OpenAI 嵌入模型获取嵌入向量，并存储在 Chroma 中
my_embedding=OpenAIEmbeddings(model="text-embedding-ada-002",openai_api_key=openai.api_key ,openai_api_base=openai.api_base)

加载知识文档、切割、存入到向量数据库

In [13]:
from langchain_text_splitters import CharacterTextSplitter

# load the document and split it into chunks
loader = TextLoader("./data/消失的她.txt")
documents = loader.load()

# split it into chunks
text_splitter = CharacterTextSplitter(chunk_size=1000, chunk_overlap=0)
docs = text_splitter.split_documents(documents)

# load it into Chroma
db = Chroma.from_documents(docs, my_embedding)

测试

In [14]:
query = "《消失的她》这部电影里主要讲的是一个什么故事？"
docs = db.similarity_search(query)
print(docs[0].page_content)

综上所述，《消失的她》是一部充满悬疑和反转的电影，通过精心构建的剧情、角色设定和悬念设置，吸引观众的注意力并让他们对真相充满好奇。影片的主题也深刻探讨了女性的力量、正义和珍惜生命的价值观。这些元素共同构成了这部引人入胜的电影。


## 7. Retrievers

### 7.1 介绍

在信息检索和自然语言处理任务中，Retrievers（检索器）是一种用于从大量文档中检索与给定查询相关的文档或信息片段的工具。
在 Langchain 这个项目中，Retrievers 的作用是从预先构建的文档向量存储（例如 FAISS）中找到与输入查询最相关的文档或文本片段。

通常，Retrievers 会执行以下步骤：

将输入查询转换为向量表示（通常使用词嵌入或预训练的语言模型）。

在向量存储中搜索与查询向量最相似的文档向量（通常使用余弦相似度或欧几里得距离等度量方法）。

返回与查询最相关的文档或文本片段，以及它们的相似度得分。

### 7.2 官方文档及参考代码

Langchain内置了很多检索策略，目录见如下页面

[https://python.langchain.com/v0.2/docs/integrations/retrievers/](https://python.langchain.com/v0.2/docs/integrations/retrievers/) 

[https://python.langchain.com/v0.1/docs/integrations/retrievers/](https://python.langchain.com/v0.1/docs/integrations/retrievers/) 

每种检索策略都提供了使用方法和参考代码，例如：

KNN检索策略：[https://python.langchain.com/v0.2/docs/integrations/retrievers/knn/](https://python.langchain.com/v0.2/docs/integrations/retrievers/knn/) 

借助ElasticSearch构建检索器：[https://python.langchain.com/v0.2/docs/integrations/retrievers/elasticsearch_retriever/](https://python.langchain.com/v0.2/docs/integrations/retrievers/elasticsearch_retriever/)


### 7.3 代码演示

In [15]:
from langchain_community.retrievers import KNNRetriever
from langchain_openai import OpenAIEmbeddings

In [16]:
retriever = KNNRetriever.from_texts(
    ["foo", "bar", "world", "hello", "foo bar"], my_embedding
)

In [17]:
result = retriever.invoke("foo")

In [18]:
result

[Document(page_content='foo'),
 Document(page_content='foo bar'),
 Document(page_content='hello'),
 Document(page_content='bar')]